## DataFrames and queries

Simple example ... a stochastic simulation for the Euler number:

In [1]:
function simulate_e()
    jumps = Float64[]
    while true
        push!(jumps, rand())  # rand is uniform in [0, 1)
        sum(jumps) > 1.0 && return jumps
    end
end

simulate_e (generic function with 1 method)

In [2]:
using DataFrames

df = DataFrame()
for i in 1:10^7
    push!(df, (id=i, pos=simulate_e()))
end

df

10000000×2 DataFrame
      Row │ id        pos                               
          │ Int64     Array…                            
──────────┼─────────────────────────────────────────────
        1 │        1  [0.094492, 0.282933, 0.575622, 0…
        2 │        2  [0.0503571, 0.770484, 0.796303]
        3 │        3  [0.986898, 0.0233961]
        4 │        4  [0.662014, 0.387601]
        5 │        5  [0.950748, 0.974857]
        6 │        6  [0.992544, 0.297129]
        7 │        7  [0.706069, 0.585499]
        8 │        8  [0.136005, 0.584358, 0.383802]
        9 │        9  [0.935809, 0.361744]
       10 │       10  [0.486501, 0.279779, 0.859927]
       11 │       11  [0.399972, 0.58345, 0.295571]
    ⋮     │    ⋮                      ⋮
  9999991 │  9999991  [0.651391, 0.131471, 0.200922, 0…
  9999992 │  9999992  [0.792001, 0.179509, 0.733391]
  9999993 │  9999993  [0.911932, 0.504674]
  9999994 │  9999994  [0.616756, 0.0180354, 0.670734]
  9999995 │  9999995  [0.141659, 0.638196, 0.350302]
  9999996 │  9999996  [0.810993, 0.838962]
  9999997 │  9999997  [0.197667, 0.0195473, 0.109984, …
  9999998 │  9999998  [0.875467, 0.152622]
  9999999 │  9999999  [0.603223, 0.65615]
 10000000 │ 10000000  [0.89079, 0.662992]
                                    9999979 rows omitted

In [3]:
transform!(df, :pos => ByRow(length) => :jumps)

10000000×3 DataFrame
      Row │ id        pos                                jumps 
          │ Int64     Array…                             Int64 
──────────┼────────────────────────────────────────────────────
        1 │        1  [0.094492, 0.282933, 0.575622, 0…      4
        2 │        2  [0.0503571, 0.770484, 0.796303]        3
        3 │        3  [0.986898, 0.0233961]                  2
        4 │        4  [0.662014, 0.387601]                   2
        5 │        5  [0.950748, 0.974857]                   2
        6 │        6  [0.992544, 0.297129]                   2
        7 │        7  [0.706069, 0.585499]                   2
        8 │        8  [0.136005, 0.584358, 0.383802]         3
        9 │        9  [0.935809, 0.361744]                   2
       10 │       10  [0.486501, 0.279779, 0.859927]         3
       11 │       11  [0.399972, 0.58345, 0.295571]          3
    ⋮     │    ⋮                      ⋮                    ⋮
  9999991 │  9999991  [0.651391, 0.131471, 0.200922, 0…      4
  9999992 │  9999992  [0.792001, 0.179509, 0.733391]         3
  9999993 │  9999993  [0.911932, 0.504674]                   2
  9999994 │  9999994  [0.616756, 0.0180354, 0.670734]        3
  9999995 │  9999995  [0.141659, 0.638196, 0.350302]         3
  9999996 │  9999996  [0.810993, 0.838962]                   2
  9999997 │  9999997  [0.197667, 0.0195473, 0.109984, …      6
  9999998 │  9999998  [0.875467, 0.152622]                   2
  9999999 │  9999999  [0.603223, 0.65615]                    2
 10000000 │ 10000000  [0.89079, 0.662992]                    2
                                           9999979 rows omitted

In [4]:
mean(df.jumps)

2.7186732

In [5]:
MathConstants.e

ℯ = 2.7182818284590...

In [6]:
using Pipe

# Number of jumps:
jumps_agg = @pipe df |>
                  groupby(_, :jumps, sort=true) |>
                  combine(_, :jumps => length)

10×2 DataFrame
 Row │ jumps  jumps_length 
     │ Int64  Int64        
─────┼─────────────────────
   1 │     2       4998368
   2 │     3       3334035
   3 │     4       1250410
   4 │     5        333212
   5 │     6         69953
   6 │     7         11989
   7 │     8          1780
   8 │     9           221
   9 │    10            31
  10 │    11             1

In [7]:
transform!(jumps_agg,
           :jumps_length => (x -> x ./ sum(x)) => :simulation,
           :jumps => ByRow(x -> (x-1) / factorial(x)) => :theory)

10×4 DataFrame
 Row │ jumps  jumps_length  simulation  theory      
     │ Int64  Int64         Float64     Float64     
─────┼──────────────────────────────────────────────
   1 │     2       4998368   0.499837   0.5
   2 │     3       3334035   0.333404   0.333333
   3 │     4       1250410   0.125041   0.125
   4 │     5        333212   0.0333212  0.0333333
   5 │     6         69953   0.0069953  0.00694444
   6 │     7         11989   0.0011989  0.00119048
   7 │     8          1780   0.000178   0.000173611
   8 │     9           221   2.21e-5    2.20459e-5
   9 │    10            31   3.1e-6     2.48016e-6
  10 │    11             1   1.0e-7     2.50521e-7

## Gaussian process regression

In [8]:
using Stheno

# Generate some synthetic data
N = 100
x = 2π * rand(N)
y = sin.(x) + 0.05*randn(N)

# Construct a squared exponential kernel σ² exp(-||x-x'||^2 / 2l²)
K(l, σ²) = σ² * stretch(EQ(), 1 / l)

# Setup zero-mean GP with this kernel (l = 1.0, σ² = 1.0)
f = GP(K(1.0, 1.0), GPC())

# Sample from this GP (with some IID observation noise)
# which is put on the diagonal of the Kernel
σ²ₙ = 0.05
fx = f(x, σ²ₙ)

# Compute posterior over f
f_posterior = f | Obs(fx, y)

# Plot it all
using Plots
plt = plot();
scatter!(plt, x, y; color=:red, label="");

x_plot = range(-0.5, 6.7; length=1000);
plot!(plt, f_posterior(x_plot); samples=10, label="", color=:blue)

In [9]:
# Hyperparameter optimisation
using Optim
using Zygote

# Unpack hyperparameters (given in log scale)
# Fudge term to avoid nasty zeros ...
unpack(θ) = exp.(θ) .+ 1e-6

# nlml = negative log marginal likelihood (of θ)
function nlml(θ)
    l, σ², σ²ₙ = unpack(θ)
    f = GP(K(l, σ²), GPC()) 
    -logpdf(f(x, σ²ₙ), y)
end

function unpack(θ)
    σ² = exp(θ[1]) + 1e-6
    l = exp(θ[2]) + 1e-6
    σ²_n = exp(θ[3]) + 1e-6
    return σ², l, σ²_n
end

# nlml = negative log marginal likelihood (of θ)
function nlml(θ)
    σ², l, σ²_n = unpack(θ)
    k = σ² * stretch(EQ(), 1 / l)
    f = GP(k, GPC())
    return -logpdf(f(x, σ²_n), y)
end

# Optimise using BFGS with adjoint-mode autodiff on nlml
θ0 = randn(3);
# results = Optim.optimize(nlml, nlml', θ0, BFGS(); inplace=false)
# results = Optim.optimize(nlml, θ->gradient(nlml, θ)[1], θ0, BFGS(); inplace=false)
# l_opt, σ²_opt, σ²ₙ_opt = unpack(results.minimizer)
results = Optim.optimize(nlml, θ0, NelderMead())
σ²_opt, l_opt, σ²ₙ_opt = unpack(results.minimizer)

@show σ²_opt
@show l_opt
@show σ²ₙ_opt

# Optimal GP and posterior
f_opt = GP(K(l_opt, σ²_opt), GPC())
f_posterior_opt = f_opt | Obs(f_opt(x, σ²ₙ_opt), y)

# Add to plot ...
plot!(plt, f_posterior_opt(x_plot); samples=10, label="", color=:green)

σ²_opt = 2.034133548770679
l_opt = 2.2446410966744126
σ²ₙ_opt = 0.002794534683382626
